In [5]:
import pandas as pd
import numpy as np
#mport torch
#import torch.nn as nn
#import torch.optim as optim
#from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
import math
import matplotlib.pyplot as plt
#from google.colab import drive
import os
import random
from tensorflow.keras.layers import Input, Dense, Dropout, concatenate
from tensorflow.keras.models import Model

In [6]:
directory_path_train = r'C:\Users\debji\Desktop\deb\Thesis\data\train_files'
directory_path_test = r'C:\Users\debji\Desktop\deb\Thesis\data\test_files'
save_path = r'C:\Users\debji\Desktop\deb\Thesis\data\runs'

In [7]:
train_list = [file for file in os.listdir(directory_path_train) if file.endswith('.csv')]
test_list = [file for file in os.listdir(directory_path_test) if file.endswith('.csv')]

In [8]:
test_list

['HF3_384cpd.csv', 'HF5_768cpd.csv', 'LF1_384cpd.csv', 'MF3_384cpd.csv']

In [9]:
train_list

['HF1_384cpd.csv',
 'HF2_384cpd.csv',
 'HF4_768cpd.csv',
 'HF6_768cpd.csv',
 'HF7_384cpd.csv',
 'LF2_384cpd.csv',
 'LF3_384cpd.csv',
 'LF4_384cpd.csv',
 'LF5_384cpd.csv',
 'LF6_384cpd.csv',
 'MF1_384cpd.csv',
 'MF2_384cpd.csv',
 'MF4_384cpd.csv',
 'MF5_384cpd.csv',
 'MF6_384cpd.csv']

In [10]:
train_list[0].split('_')[0]

'HF1'

In [11]:
# Sample data
flow_type = ['LF1', 'LF2', 'LF3', 'LF4', 'LF5', 'LF6', 'MF1', 'MF2', 'MF3', 'MF4', 'MF5', 'MF6', 'HF1', 'HF2', 'HF3', 'HF4', 'HF5', 'HF6', 'HF7']
amplitude_pow = [3, 4, 5, 6, 6.5, 7, 4, 5, 5.5, 6, 6.5, 7, 5, 6, 7, 7.25, 7.5, 8, 9]
frequency = [2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 4, 4, 4, 4, 4, 4, 4]
tau = 0.2
rho = 1
nu = 1
d = 1
k = (math.pow(d,2))*1.731e-4
# Create a dictionary where each string x value corresponds to a pair of numbers (y, z)
mapping = {x: (y, z) for x, y, z in zip(flow_type, amplitude_pow, frequency)}

In [12]:
k

0.0001731

In [13]:
mapping

{'LF1': (3, 2),
 'LF2': (4, 2),
 'LF3': (5, 2),
 'LF4': (6, 2),
 'LF5': (6.5, 2),
 'LF6': (7, 2),
 'MF1': (4, 3),
 'MF2': (5, 3),
 'MF3': (5.5, 3),
 'MF4': (6, 3),
 'MF5': (6.5, 3),
 'MF6': (7, 3),
 'HF1': (5, 4),
 'HF2': (6, 4),
 'HF3': (7, 4),
 'HF4': (7.25, 4),
 'HF5': (7.5, 4),
 'HF6': (8, 4),
 'HF7': (9, 4)}

In [14]:
def nondimensionalize(rho, nu, k, dudt, gradp, t):
  nd_dudt = [x/((math.pow(nu,2))*(math.pow(k,-1.5))) for x in dudt]
  nd_gradp = [x/(rho*(math.pow(nu,2))*(math.pow(k,-1.5))) for x in gradp]
  nd_t = [x*nu/k for x in t]
  return nd_dudt, nd_gradp, nd_t

def dimensionalize(rho, nu, k, ndim_dudt, ndim_gradp, ndim_t):
  dim_dudt = [x*((math.pow(nu,2))*(math.pow(k,-1.5))) for x in ndim_dudt]
  dim_gradp = [x*(rho*(math.pow(nu,2))*(math.pow(k,-1.5))) for x in ndim_gradp]
  dim_t = [x*k/nu for x in ndim_t]
  return dim_dudt, dim_gradp, dim_t

def data_preparation(data, amp):
  data = data.dropna()
  time_series = data['TIME']
  ubulk_series = data['UBULK']
  # Initialize an empty list to store the calculated gradients
  dudt = []
  grad_pressures =[]
  times = []
  epsilon = 1 - ((math.pi)/(3*math.sqrt(2)))
  # Calculate the gradient using central difference for each odd position starting from 1
  for i in range(1, len(data) - 1, 2):
      # Central difference scheme: (f[i+1] - f[i-1]) / (t[i+1] - t[i-1])
      time_derivative = (ubulk_series[i + 1] - ubulk_series[i - 1]) / (time_series[i + 1] - time_series[i - 1])
      pressure = epsilon*math.pow(10,amp)*math.sin(100*time_series[i])
      dudt.append(time_derivative)
      grad_pressures.append(pressure)
      times.append(time_series[i])

  # Create a new DataFrame to store the results
  #result_df = pd.DataFrame({'Position': list(range(1, 5997, 2)), 'Gradient_UBULK': gradients, 'Pressure_term': pressures, 'Time': times})
  dudt_non_dim, grad_p_non_dim, time_non_dim = nondimensionalize(rho, nu, k, dudt, grad_pressures, times)
  result_df = pd.DataFrame({'Gradient_UBULK': dudt_non_dim, 'Pressure_term': grad_p_non_dim, 'Time': time_non_dim})
  return result_df
  # Display the result
  #print(result_df)

In [15]:
# Loop through each CSV file
columns = ['Gradient_UBULK', 'Pressure_term', 'Time']
datas = []
# Initialize an empty DataFrame with specified columns
merged_df = pd.DataFrame(columns=columns)
for file in train_list:
    # Construct the full path to the CSV file
    file_path = os.path.join(directory_path_train, file)

    # Read the CSV file into a DataFrame
    df = pd.read_csv(file_path)
    if file.split('_')[0] in mapping:
      result = data_preparation(df, mapping[file.split('_')[0]][0])
      df_final = pd.DataFrame(result, columns=['Gradient_UBULK', 'Pressure_term', 'Time'])
      for i in range(1,6):
        df_final[f'Gradient_UBULK_lag{i}'] = np.interp(df_final['Time'] - i*tau, df_final['Time'], df_final['Gradient_UBULK'], left=0)
      datas.append(df_final)
        #df_final[f'Gradient_UBULK_lag{i}'] = np.interp(df_final['Time'],df_final['Gradient_UBULK'], df_final['Time'] - i*tau, left = 0)
      print(df_final)
      print("*"*20)
      # Create lag features
      #for i in range(1, 6):
      #    df_final[f'Gradient_UBULK_lag{i}'] = df_final['Gradient_UBULK'].shift(i)
      #df_final = df_final.dropna().reset_index(drop=True)
      merged_df = pd.concat([merged_df, df_final], ignore_index=True)
    # Now you can use the data in the DataFrame df as needed
    # For example, you can print the first few rows of the DataFrame

       Gradient_UBULK  Pressure_term       Time  Gradient_UBULK_lag1  \
0            0.000443       0.000008   0.007350             0.000000   
1            0.000874       0.000015   0.014610             0.000000   
2            0.001300       0.000022   0.021870             0.000000   
3            0.001722       0.000030   0.029129             0.000000   
4            0.002140       0.000037   0.036389             0.000000   
...               ...            ...        ...                  ...   
10218        0.005720       0.056692  74.185961             0.015197   
10219        0.005356       0.056694  74.193221             0.014878   
10220        0.004991       0.056697  74.200480             0.014557   
10221        0.004626       0.056699  74.207740             0.014234   
10222        0.004259       0.056701  74.214999             0.013908   

       Gradient_UBULK_lag2  Gradient_UBULK_lag3  Gradient_UBULK_lag4  \
0                 0.000000             0.000000             0.0

C:\Users\debji\AppData\Local\Temp\ipykernel_18368\3073928088.py:25: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  merged_df = pd.concat([merged_df, df_final], ignore_index=True)


      Gradient_UBULK  Pressure_term       Time  Gradient_UBULK_lag1  \
0           0.004426       0.000075   0.007350             0.000000   
1           0.008738       0.000149   0.014610             0.000000   
2           0.012999       0.000224   0.021870             0.000000   
3           0.017218       0.000298   0.029129             0.000000   
4           0.021397       0.000372   0.036389             0.000000   
...              ...            ...        ...                  ...   
9945       -0.137264       0.560859  72.204090            -0.217697   
9946       -0.133973       0.560882  72.211349            -0.215180   
9947       -0.130660       0.560906  72.218609            -0.212628   
9948       -0.127327       0.560929  72.225868            -0.210043   
9949       -0.123974       0.560952  72.233128            -0.207425   

      Gradient_UBULK_lag2  Gradient_UBULK_lag3  Gradient_UBULK_lag4  \
0                0.000000             0.000000             0.000000   
1    

In [16]:
import matplotlib.pyplot as plt

df_final = datas[0]

#plt.plot(df_final['Time'],df_final['Gradient_UBULK'])
#plt.plot(df_final['Time'],df_final['Gradient_UBULK_lag1'])
#plt.plot(df_final['Time'],df_final['Gradient_UBULK_lag2'])
#plt.plot(df_final['Time'],df_final['Gradient_UBULK_lag3'])
#plt.plot(df_final['Time'],df_final['Gradient_UBULK_lag4'])
#plt.plot(df_final['Time'],df_final['Gradient_UBULK_lag5'])
#plt.show()

import plotly.graph_objects as go

# Create traces for each line plot
trace1 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK'], mode='lines', name='Gradient_UBULK')
trace2 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK_lag1'], mode='lines', name='Gradient_UBULK_lag1')
trace3 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK_lag2'], mode='lines', name='Gradient_UBULK_lag2')
trace4 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK_lag3'], mode='lines', name='Gradient_UBULK_lag3')
trace5 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK_lag4'], mode='lines', name='Gradient_UBULK_lag4')
trace6 = go.Scatter(x=df_final['Time'], y=df_final['Gradient_UBULK_lag5'], mode='lines', name='Gradient_UBULK_lag5')

# Create figure and add traces
fig = go.Figure(data=[trace1, trace2, trace3, trace4, trace5, trace6])

# Update layout
fig.update_layout(title='Time vs Gradient_UBULK with Lagged Values',
                  xaxis_title='Time',
                  yaxis_title='Gradient_UBULK')

# Show plot
fig.show()

In [17]:
merged_df

Gradient_UBULK  Pressure_term       Time  Gradient_UBULK_lag1  \
0            0.000443       0.000008   0.007350             0.000000   
1            0.000874       0.000015   0.014610             0.000000   
2            0.001300       0.000022   0.021870             0.000000   
3            0.001722       0.000030   0.029129             0.000000   
4            0.002140       0.000037   0.036389             0.000000   
...               ...            ...        ...                  ...   
44310       -0.044908       5.838774  81.743116            -0.010636   
44311       -0.046182       5.839922  81.815712            -0.031218   
44312       -0.041531       5.841060  81.888308            -0.041538   
44313       -0.027767       5.842190  81.960904            -0.045220   
44314       -0.008727       5.843310  82.033500            -0.045043   

       Gradient_UBULK_lag2  Gradient_UBULK_lag3  Gradient_UBULK_lag4  \
0                 0.000000             0.000000             0.000000   
1                 0.000000             0.000000             0.000000   
2                 0.000000             0.000000             0.000000   
3                 0.000000             0.000000             0.000000   
4                 0.000000             0.000000             0.000000   
...                    ...                  ...                  ...   
44310             0.064581             0.126055             0.134164   
44311             0.037795             0.106501             0.140563   
44312             0.009588             0.083430             0.136788   
44313            -0.016344             0.058293             0.122504   
44314            -0.034212             0.030944             0.101263   

       Gradient_UBULK_lag5  
0                 0.000000  
1                 0.000000  
2                 0.000000  
3                 0.000000  
4                 0.000000  
...                    ...  
44310             0.102484  
44311             0.113053  
44312             0.125140  
44313             0.135817  
44314             0.139792  

[44315 rows x 8 columns]

In [18]:
# Initialize an empty DataFrame with specified columns
test_df = []
for file in test_list:
    # Construct the full path to the CSV file
    file_path1 = os.path.join(directory_path_test, file)

    # Read the CSV file into a DataFrame
    df1 = pd.read_csv(file_path1)
    if file.split('_')[0] in mapping:
      result1 = data_preparation(df1, mapping[file.split('_')[0]][0])
      test = pd.DataFrame(result1, columns=['Gradient_UBULK', 'Pressure_term', 'Time'])
      for i in range(1,6):
        test[f'Gradient_UBULK_lag{i}'] = np.interp(test['Time'] - i*tau, test['Time'], test['Gradient_UBULK'], left=0)
      test_df.append(test)
        #df_final[f'Gradient_UBULK_lag{i}'] = np.interp(df_final['Time'],df_final['Gradient_UBULK'], df_final['Time'] - i*tau, left = 0)
      print(test)
      print("*"*20)

      Gradient_UBULK  Pressure_term       Time  Gradient_UBULK_lag1  \
0           0.044264       0.000752   0.007350             0.000000   
1           0.087380       0.001495   0.014610             0.000000   
2           0.129993       0.002237   0.021870             0.000000   
3           0.172175       0.002980   0.029129             0.000000   
4           0.213972       0.003723   0.036389             0.000000   
...              ...            ...        ...                  ...   
3154        2.466844       2.282384  22.904134             2.889099   
3155        2.445591       2.283069  22.911394             2.879540   
3156        2.423950       2.283754  22.918653             2.869532   
3157        2.401923       2.284439  22.925913             2.859076   
3158        2.379512       2.285124  22.933173             2.848173   

      Gradient_UBULK_lag2  Gradient_UBULK_lag3  Gradient_UBULK_lag4  \
0                0.000000             0.000000             0.000000   
1    

In [19]:
test_final = test_df[2]

import plotly.graph_objects as go

# Create traces for each line plot
trace1 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK'], mode='lines', name='Gradient_UBULK')
trace2 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK_lag1'], mode='lines', name='Gradient_UBULK_lag1')
trace3 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK_lag2'], mode='lines', name='Gradient_UBULK_lag2')
trace4 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK_lag3'], mode='lines', name='Gradient_UBULK_lag3')
trace5 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK_lag4'], mode='lines', name='Gradient_UBULK_lag4')
trace6 = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK_lag5'], mode='lines', name='Gradient_UBULK_lag5')

# Create figure and add traces
fig1 = go.Figure(data=[trace1, trace2, trace3, trace4, trace5, trace6])

# Update layout
fig1.update_layout(title='Time vs Gradient_UBULK with Lagged Values',
                  xaxis_title='Time',
                  yaxis_title='Gradient_UBULK')

# Show plot
fig1.show()


In [30]:
import os
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout, LayerNormalization, MultiHeadAttention, Flatten, Lambda
import tensorflow as tf
from tensorflow.keras.layers import PReLU
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tensorflow.keras.initializers import GlorotUniform
from tensorflow.keras.models import load_model


# Define Huber loss function
def huber_loss(y_true, y_pred, delta=1.0):
    error = y_true - y_pred
    m_gt = tf.reduce_mean(y_true)
    rms_gt = tf.reduce_mean(tf.square(y_true))
    huber_loss = tf.where(tf.abs(error) < delta, 0.5 * tf.square(error), delta * (tf.abs(error) - 0.5 * delta))
    return tf.reduce_mean(huber_loss)

def mse_loss_normalized(y_true, y_pred):
    # Compute MSE loss
    mse_loss = tf.reduce_mean(tf.square(y_true - y_pred))

    # Compute RMS value of the ground truth output
    rms_gt = tf.reduce_mean(tf.square(y_true))

    # Normalize MSE loss
    normalized_loss = mse_loss / rms_gt

    return normalized_loss

def silu(x):
    return x * tf.sigmoid(x)

def inception_block(input_layer, num_filters=(64, 128, 32)):
    """Create an Inception-like block with dense layers."""
    # Define the number of layers in each branch
    num_layers = len(num_filters)
    num_branches = 3
    # Initialize a list to store outputs of each branch
    branch_outputs = []
    
    # Create branches with the same number of layers
    for i in range(num_branches):
        # Add dense layers to each branch
        branch = input_layer
        for _ in range(num_layers):
            branch = Dense(num_filters[i], activation='relu')(branch)
        # Append the output of the branch to the list
        branch_outputs.append(branch)
    
    # Concatenate the outputs of all branches
    concat = concatenate(branch_outputs, axis=-1)
    return concat

# Register the SiLU activation function with TensorFlow/Keras
tf.keras.utils.get_custom_objects()['silu'] = silu

# Remove the 'Time' column
data = merged_df.drop(columns=['Time'])

# Split dataset into input (X) and output (y)
X = data.drop(columns=['Gradient_UBULK'])
y = data['Gradient_UBULK']

existing = r'C:\Users\debji\Desktop\deb\Thesis\data\runs\train_inception_huber2\model.keras'

################################## Simple NN #############################################
# model = Sequential([
#      Dense(64, activation='relu', kernel_initializer=GlorotUniform(), input_shape=(X.shape[1],)),
#      Dense(32, activation='relu', kernel_initializer=GlorotUniform()),
#      Dense(1, kernel_initializer=GlorotUniform())  # Output layer
# ])
#X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
#Standardize the input features
# scaler = StandardScaler()
# X_train_scaled = scaler.fit_transform(X)
#X_test_scaled = scaler.transform(X)

# model = Sequential([
#      Dense(64, activation='tanh', input_shape=(X.shape[1],)),
#      Dense(32, activation='tanh'),
#      Dense(1)  # Output layer
# ])

# Build the neural network model with increased complexity and specified activations
# model = Sequential([
#    Dense(128, activation='relu', kernel_initializer=GlorotUniform(), input_shape=(X.shape[1],)),  # Increase the number of neurons
#    Dropout(0.2),  # Add dropout regularization to prevent overfitting
#   Dense(64, activation='relu', kernel_initializer=GlorotUniform()),  # Add another hidden layer
#    Dropout(0.2),
#    Dense(32, activation='relu', kernel_initializer=GlorotUniform()),  # Add another hidden layer
#    Dropout(0.2),
#    Dense(16, activation= 'relu', kernel_initializer=GlorotUniform()),  # Add another hidden layer
#    PReLU(),  # Parametric ReLU activation
#    Dense(1,  kernel_initializer=GlorotUniform())  # Output layer
# ])

############### ENCODER_DECODER BLOCK###################

# Define input shape (change this to match your data)
# input_shape = (X.shape[1],)

# # Define the input layer
# inputs = Input(shape=input_shape)

# # Encoder
# dense1 = Dense(32, activation='relu', kernel_initializer='glorot_uniform')(inputs)
# dense1 = Dense(32, activation='relu', kernel_initializer='glorot_uniform')(dense1)
# dense1 = Dropout(0.2)(dense1)

# dense2 = Dense(64, activation='relu', kernel_initializer='glorot_uniform')(dense1)
# dense2 = Dense(64, activation='relu', kernel_initializer='glorot_uniform')(dense2)
# dense2 = Dropout(0.2)(dense2)

# dense3 = Dense(128, activation='relu', kernel_initializer='glorot_uniform')(dense2)
# dense3 = Dense(128, activation='relu', kernel_initializer='glorot_uniform')(dense3)
# dense3 = Dropout(0.2)(dense3)

# # dense4 = Dense(256, activation='relu', kernel_initializer='glorot_uniform')(dense3)
# # dense4 = Dense(256, activation='relu', kernel_initializer='glorot_uniform')(dense4)
# # dense4 = Dropout(0.2)(dense4)

# # Bottleneck
# dense5 = Dense(256, activation='relu', kernel_initializer='glorot_uniform')(dense3)
# dense5 = Dropout(0.2)(dense5)

# # Decoder
# # dense6 = Dense(256, activation='relu', kernel_initializer='glorot_uniform')(dense5)
# # dense6 = Dense(256, activation='relu', kernel_initializer='glorot_uniform')(dense6)

# dense7 = Dense(128, activation='relu', kernel_initializer='glorot_uniform')(dense5)
# dense7 = Dense(128, activation='relu', kernel_initializer='glorot_uniform')(dense7)

# dense8 = Dense(64, activation='relu', kernel_initializer='glorot_uniform')(dense7)
# dense8 = Dense(64, activation='relu', kernel_initializer='glorot_uniform')(dense8)

# dense9 = Dense(32, activation='relu', kernel_initializer='glorot_uniform')(dense8)
# dense9 = Dense(32, activation='relu', kernel_initializer='glorot_uniform')(dense9)

# # Output layer
# outputs = Dense(1, activation='linear', kernel_initializer='glorot_uniform')(dense9)

# # Create model
# model = Model(inputs=inputs, outputs=outputs)

# # Print model summary
# model.summary()


#################### INCEPTION BLOCK #####################

# Define input layer
input_layer = Input(shape=(X.shape[1],))

# Add inception block with three branches
output_layer = inception_block(input_layer, num_filters=(32, 64, 128))

# Add output layer for regression (linear activation)
output_layer = Dense(1, activation='linear')(output_layer)

# Create model
#model = Model(inputs=input_layer, outputs=output_layer)
#model = load_model(existing)
##for custom loss
model = load_model(existing, custom_objects={'huber_loss': huber_loss})


# Compile model
#model.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model.compile(optimizer='adam', loss=huber_loss, metrics=['mae'])

# Print model summary
model.summary()

###############################################################

# Compile the model
#model.compile(optimizer='adam', loss='mse')
#model.compile(optimizer='adam', loss=huber_loss)

# Train the model and store the history
history = model.fit(X, y, epochs=50, batch_size=32, validation_split=0.2)

# Create a folder to save plots and the trained model
folder_name = input("Enter the folder name to save plots and the trained model: ")
plot_save_path = os.path.join(save_path,folder_name)
os.makedirs(plot_save_path, exist_ok=True)

# Create Plotly figure
fig3 = make_subplots(rows=1, cols=1)

# Add training loss trace
fig3.add_trace(go.Scatter(x=history.epoch, y=history.history['loss'], mode='lines', name='Training Loss'))

# Add validation loss trace
fig3.add_trace(go.Scatter(x=history.epoch, y=history.history['val_loss'], mode='lines', name='Validation Loss'))

# Update layout
fig3.update_layout(title='Training and Validation Loss',
                  xaxis_title='Epoch',
                  yaxis_title='Loss')

# Save the plot
loss_plot_path = os.path.join(plot_save_path, 'loss_plot.html')
fig3.write_html(loss_plot_path)

# Show plot
fig3.show()


# Save the trained model
model.save(os.path.join(plot_save_path, 'model.keras'))

# Plot and save test_df plots
counter = 0
for test_final in test_df:
    new_data_processed = test_final.drop(columns=['Time', 'Gradient_UBULK'])
    predictions = model.predict(new_data_processed)

    trace_actual = go.Scatter(x=test_final['Time'], y=test_final['Gradient_UBULK'], mode='lines', name='Actual Gradient_UBULK')
    trace_predicted = go.Scatter(x=test_final['Time'], y=predictions.flatten(), mode='lines', name='Predicted Gradient_UBULK')
    fig2 = go.Figure(data=[trace_actual, trace_predicted])
    fig2.update_layout(title='Actual_Gradient_UBULK vs Predicted_Gradient_UBULK', xaxis_title='Time', yaxis_title='Gradient_UBULK')
    
    plot_path = os.path.join(plot_save_path, f"{test_list[counter].split('.')[0]}_prediction.html")
    fig2.write_html(plot_path)
    counter += 1

print("Plots and trained model saved successfully!")

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_3       │ (None, 6)         │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_30 (Dense)    │ (None, 32)        │        224 │ input_layer_3[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_33 (Dense)    │ (None, 64)        │        448 │ input_layer_3[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_36 (Dense)    │ (None, 128)       │        896 │ input_layer_3[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_31 (Dense)    │ (None, 32)        │      1,056 │ dense_30[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_34 (Dense)    │ (None, 64)        │      4,160 │ dense_33[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_37 (Dense)    │ (None, 128)       │     16,512 │ dense_36[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_32 (Dense)    │ (None, 32)        │      1,056 │ dense_31[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_35 (Dense)    │ (None, 64)        │      4,160 │ dense_34[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_38 (Dense)    │ (None, 128)       │     16,512 │ dense_37[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_3       │ (None, 224)       │          0 │ dense_32[0][0],   │
│ (Concatenate)       │                   │            │ dense_35[0][0],   │
│                     │                   │            │ dense_38[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_39 (Dense)    │ (None, 1)         │        225 │ concatenate_3[0]… │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 45,249 (176.75 KB)

 Trainable params: 45,249 (176.75 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 6s 2ms/step - loss: 0.7406 - mae: 0.8617 - val_loss: 0.0058 - val_mae: 0.0608
Epoch 2/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 0.7528 - mae: 0.8767 - val_loss: 0.0091 - val_mae: 0.1093
Epoch 3/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 0.7412 - mae: 0.8664 - val_loss: 0.0070 - val_mae: 0.0743
Epoch 4/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 0.7155 - mae: 0.8359 - val_loss: 0.0144 - val_mae: 0.1368
Epoch 5/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step - loss: 0.6637 - mae: 0.7929 - val_loss: 0.0075 - val_mae: 0.0711
Epoch 6/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 3ms/step - loss: 0.6653 - mae: 0.7905 - val_loss: 0.0073 - val_mae: 0.0896
Epoch 7/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 3ms/step - loss: 0.7459 - mae: 0.8656 - val_loss: 0.0084 - val_mae: 0.0997
Epoch 8/50
1108/1108 ━━━━━━━━━━━━━━━━━━━━ 3s 3ms/step - loss: 0.7667 - mae: 0.8962 - val_loss: 0.0056 - val_mae: 0.0537
Epoch 9/50
1108/1108 ━━━━━━━━━━━━━━━━━━━

99/99 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step
94/94 ━━━━━━━━━━━━━━━━━━━━ 0s 894us/step
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step 
47/47 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step
Plots and trained model saved successfully!


In [20]:
import numpy as np
import pandas as pd
from scipy.fft import fft
import plotly.graph_objects as go

def analyze_signal(signal, time_series):
    print(signal)
    # Perform Fourier transform
    fft_result = fft(signal)

    # Calculate the frequencies
    sampling_rate = 1 / (time_series[1] - time_series[0])
    amplitude = np.sqrt(np.mean(np.square(signal)))
  
    n = len(signal)
    k = np.arange(n)
    T = n / sampling_rate
    frq = k/T
    frq = frq[:len(frq)//2]
    Y = np.fft.fft(signal)/n # dft and normalization
    Y = Y[:n//2]
    print(f"Y:{Y}")
    
    # Find the index corresponding to the maximum amplitude
    dominant_index = np.argmax(np.abs(Y))

    # Retrieve the corresponding frequency
    dominant_frequency = frq[dominant_index]
    

    # Calculate the mean position
    mean_position = np.mean(signal)

    #Plot the frequency spectrum
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=frq, y=abs(Y)/max(abs(Y)), mode='lines', name='Frequency Spectrum'))
    fig.update_layout(title='Frequency Spectrum',
                      xaxis_title='Frequency (Hz)',
                      yaxis_title='|Y(freq)|/max|Y|',
                      showlegend=True)

    # Return results and plotly figure
    return mean_position, dominant_frequency, amplitude, fig

# Example usage:
# Assuming df is your DataFrame with 'time' and 'signal' columns
# Replace 'time_column_name' and 'signal_column_name' with your actual column names

# Extract signal and time columns
# time_series = df['time_column_name'].values
# signal = df['signal_column_name'].values

# # Analyze signal
# fig, mean_position, dominant_frequency, dominant_amplitude = analyze_signal(signal, time_series)

In [21]:
import os
import pandas as pd
from tensorflow.keras.models import load_model

# Define the directory path where your folders are located
directory_path = r'C:\Users\debji\Desktop\deb\Thesis\data\runs'

# Get the list of all folders in the directory
all_folders = os.listdir(directory_path)

# Filter folders whose names start with "medium" or "shallow"
relevant_folders = [folder for folder in all_folders if folder.startswith(('medium', 'shallow'))]

# Define Huber loss function
def huber_loss(y_true, y_pred, delta=1.0):
    error = y_true - y_pred
    m_gt = tf.reduce_mean(y_true)
    rms_gt = tf.reduce_mean(tf.square(y_true))
    huber_loss = tf.where(tf.abs(error) < delta, 0.5 * tf.square(error), delta * (tf.abs(error) - 0.5 * delta))
    return tf.reduce_mean(huber_loss)

def mse_loss_normalized(y_true, y_pred):
    # Compute MSE loss
    mse_loss = tf.reduce_mean(tf.square(y_true - y_pred))

    # Compute RMS value of the ground truth output
    rms_gt = tf.reduce_mean(tf.square(y_true))

    # Normalize MSE loss
    normalized_loss = mse_loss / rms_gt

    return normalized_loss

# Iterate over relevant folders
for folder in relevant_folders:
    # Construct the path to the folder
    folder_path = os.path.join(directory_path, folder)
    
    # Check if "model.keras" file exists in the folder
    model_file = os.path.join(folder_path, 'model.keras')
    if os.path.exists(model_file):

        # Determine which loss function to use based on folder name
        if 'huber' in folder:
            model = load_model(model_file, custom_objects={'huber_loss': huber_loss})
        else:
            model = load_model(model_file, custom_objects={'mse_loss_normalized': mse_loss_normalized})
       
        counter = 0 
        # Iterate over each test_final in test_df
        for test_final in test_df:
            print(test_final)
            #test_final.drop(columns=['Gradient_UBULK_prediction'], inplace=True)
            new_data_processed = test_final.drop(columns=['Time', 'Gradient_UBULK'])
            predictions = model.predict(new_data_processed)
            #test_final['Gradient_UBULK_prediction'] = predictions.flatten()
            
            # Extract attributes for the actual and predicted signals
            actual_attributes = analyze_signal(test_final['Gradient_UBULK'].values, test_final['Time'].values)
            predicted_attributes = analyze_signal(predictions, test_final['Time'].values)
            actual_mean_position = actual_attributes[0]
            actual_dominant_frequency = actual_attributes[1]  # Index 2 corresponds to dominant frequency
            actual_dominant_amplitude = actual_attributes[2]  # Index 3 corresponds to dominant amplitude
            
            predicted_mean_position = predicted_attributes[0]
            predicted_dominant_frequency = predicted_attributes[1]  # Index 2 corresponds to dominant frequency
            predicted_dominant_amplitude = predicted_attributes[2]  # Index 3 corresponds to dominant amplitude
            
            # Create a text file for both actual and predicted signal attributes
            file_path = os.path.join(folder_path, f"{test_list[counter].split('.')[0]}_signal_attributes.txt")
            html_path_actual = os.path.join(folder_path, f"{test_list[counter].split('.')[0]}_spectrum_actual.html")
            html_path_predicted = os.path.join(folder_path, f"{test_list[counter].split('.')[0]}_spectrum_predicted.html")
            actual_attributes[3].write_html(html_path_actual)
            predicted_attributes[3].write_html(html_path_predicted)
            with open(file_path, 'w') as file:
                file.write(f"Actual Signal Attributes:\n")
                file.write(f"Mean Position: {actual_mean_position}\n")
                file.write(f"Dominant Frequency: {actual_dominant_frequency}\n")
                file.write(f"Dominant Amplitude: {actual_dominant_amplitude}\n\n")
                
                file.write(f"Predicted Signal Attributes:\n")
                file.write(f"Mean Position: {predicted_mean_position}\n")
                file.write(f"Dominant Frequency: {predicted_dominant_frequency}\n")
                file.write(f"Dominant Amplitude: {predicted_dominant_amplitude}\n")

            
            counter += 1
    


      Gradient_UBULK  Pressure_term       Time  Gradient_UBULK_lag1  \
0           0.044264       0.000752   0.007350             0.000000   
1           0.087380       0.001495   0.014610             0.000000   
2           0.129993       0.002237   0.021870             0.000000   
3           0.172175       0.002980   0.029129             0.000000   
4           0.213972       0.003723   0.036389             0.000000   
...              ...            ...        ...                  ...   
3154        2.466844       2.282384  22.904134             2.889099   
3155        2.445591       2.283069  22.911394             2.879540   
3156        2.423950       2.283754  22.918653             2.869532   
3157        2.401923       2.284439  22.925913             2.859076   
3158        2.379512       2.285124  22.933173             2.848173   

      Gradient_UBULK_lag2  Gradient_UBULK_lag3  Gradient_UBULK_lag4  \
0                0.000000             0.000000             0.000000   
1    

In [33]:
relevant_folders

['medium_fullsilu_adam_mse',
 'medium_relu_adam_huber',
 'medium_relu_adam_mse',
 'medium_silu_adam_mse',
 'medium_tanh_adam_mse',
 'shallow_relu_relu_adam_huber',
 'shallow_relu_relu_adam_mse',
 'shallow_relu_silu_adam_mse',
 'shallow_relu_tanh_adam_huber',
 'shallow_relu_tanh_adam_mse',
 'shallow_silu_silu_adam_mse',
 'shallow_tanh_tanh_adam_huber',
 'shallow_tanh_tanh_adam_mse']